## COLAB NOTEBOOK FOR THE FLAN-T5 RESULTS EVALUATIONS

In [2]:
!pip install --upgrade pip
!pip install unbabel-comet
!pip install ast
!pip install bert-score git+https://github.com/huggingface/evaluate@af3c30561d840b83e54fc5f7150ea58046d6af69
!pip install bert-score
!pip install git+https://github.com/google-research/bleurt.git
!pip install nltk

# Import all this required libraries
from bert_score import score
import ast
from comet import download_model, load_from_checkpoint
from evaluate import load
import evaluate
import nltk
from nltk.tokenize import word_tokenize
import json

  Using cached AST-0.0.2.tar.gz (19 kB)
  error: subprocess-exited-with-error
  
  × python setup.py egg_info did not run successfully.
  │ exit code: 1
  ╰─> See above for output.
  
  note: This error originates from a subprocess, and is likely not a problem with pip.
  Preparing metadata (setup.py) ... error
error: metadata-generation-failed

× Encountered error while generating package metadata.
╰─> See above for output.

note: This is an issue with the package mentioned above, not pip.
hint: See above for details.
  Cloning https://github.com/google-research/bleurt.git to /tmp/pip-req-build-ofpu580l
  Running command git clone --filter=blob:none --quiet https://github.com/google-research/bleurt.git /tmp/pip-req-build-ofpu580l
  Resolved https://github.com/google-research/bleurt.git to commit cebe7e6f996b40910cfaa520a63db47807e3bf5c
  Preparing metadata (setup.py) ... done


In [3]:
# Retrieve the python dictionary
data = []
with open("flant5_dict.txt", "r", encoding='utf-8') as file:
    for line in file:
        dictionary_str = line.strip()
        entry = ast.literal_eval(dictionary_str)
        data.append(entry)

### COMET-22 METRIC

In [ ]:
model_path = download_model("Unbabel/wmt22-comet-da")
model = load_from_checkpoint(model_path)
model_output = model.predict(data, batch_size=8, gpus=1)
print(model_output)
print(model_output[1])

Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.migration.utils:Lightning automatically upgraded your loaded checkpoint from v1.8.3.post1 to v1.9.5. To apply the upgrade to your files permanently, run `python -m pytorch_lightning.utilities.upgrade_checkpoint --file ../root/.cache/huggingface/hub/models--Unbabel--wmt22-comet-da/snapshots/371e9839ca4e213dde891b066cf3080f75ec7e72/checkpoints/model.ckpt`


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:IPU available: False, using: 0 IPUs
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
Predicting DataLoader 0: 100%|██████████| 9557/9557 [35:06<00:00,  4.54it/s]


Prediction([('scores', [0.8029667735099792, 0.6516153216362, 0.9075332283973694, 0.9916894435882568, 0.8713390827178955, 0.7657122015953064, 0.955665111541748, 0.8452756404876709, 0.917492687702179, 0.8452756404876709, 0.872627317905426, 0.8134823441505432, 0.8529818058013916, 0.8300104737281799, 0.7015923261642456, 0.8452756404876709, 0.5220802426338196, 0.8134823441505432, 0.8529815673828125, 0.7134742736816406, 0.7877101302146912, 0.8492302298545837, 0.6467957496643066, 0.7493925094604492, 0.8008021712303162, 0.9136127829551697, 0.8426297307014465, 0.910762369632721, 0.766531765460968, 0.689856231212616, 0.9413890242576599, 0.7506921887397766, 0.7978924512863159, 0.8140791058540344, 0.7735010981559753, 0.776245653629303, 0.7199692130088806, 0.8180970549583435, 0.7467027306556702, 0.8815730214118958, 0.7960227131843567, 0.727242112159729, 0.6247454285621643, 0.9453834295272827, 0.5832821726799011, 0.7246062755584717, 0.5973723530769348, 0.6667766571044922, 0.6538702249526978, 0.67870

In [ ]:
flant5_score = model_output[0]
flant5_score.append(model_output[1])

with open("flant5_comet22.txt", "w") as file:
    for number in flant5_score:
        file.write(str(number) + "\n")

#with open("gpt_comet22.txt", "r") as file:
#    numbers = [int(line.strip()) for line in file.readlines()]

In [4]:
# Since we no longer need the source sentences, we can just get a list with the predictions/hypothesis and a list with the references

predictions = [dictio['mt'] for dictio in data]
references = [dictio['ref'] for dictio in data]

## BERTScore METRIC

In [ ]:
bertscore = load("bertscore")
bert_output = bertscore.compute(predictions=predictions, references=references, lang="en")
print('Precision: ', sum(bert_output['precision'])/len(bert_output['precision']))
print('Recall: ', sum(bert_output['recall'])/len(bert_output['recall']))
print('F1: ', sum(bert_output['f1'])/len(bert_output['f1']))

In [ ]:
flant5_bert_score = bert_output['precision']
flant5_bert_score.append(sum(flant5_bert_score)/len(flant5_bert_score))

flant5_bert_recall = bert_output['recall']
flant5_bert_recall.append(sum(flant5_bert_recall)/len(flant5_bert_recall))

flant5_bert_f1 = bert_output['f1']
flant5_bert_f1.append(sum(flant5_bert_f1)/len(flant5_bert_f1))

with open("flant5_bert_score.txt", "w") as file:
    for number in flant5_bert_score:
        file.write(str(number) + "\n")

with open("flant5_bert_recall.txt", "w") as file:
    for number in flant5_bert_recall:
        file.write(str(number) + "\n")

with open("flant5_bert_f1.txt", "w") as file:
    for number in flant5_bert_f1:
        file.write(str(number) + "\n")

In [ ]:
from bert_score import score
import numpy as np

batch_size = 100  # Number of pairs to process in each batch
# Calculate the total number of batches
num_batches = int(np.ceil(len(predictions) / batch_size))

# Compute BERTScore batch-wise
avg_P, avg_R, avg_F1 = 0, 0, 0
for batch_idx in range(num_batches):
    start_idx = batch_idx * batch_size
    end_idx = min((batch_idx + 1) * batch_size, len(predictions))

    # Extract batch of candidates and references
    batch_candidates = predictions[start_idx:end_idx]
    batch_references = references[start_idx:end_idx]

    # Compute BERTScore for the batch
    P, R, F1 = score(batch_candidates, batch_references, lang='en', verbose=True)

    # Accumulate the scores
    avg_P += P.sum().item()
    avg_R += R.sum().item()
    avg_F1 += F1.sum().item()

    print("Batch ", batch_idx, 'from ', num_batches, "P,R,F1:", avg_P,avg_R,avg_F1)

# Calculate the average scores
avg_P /= len(predictions)
avg_R /= len(predictions)
avg_F1 /= len(predictions)

# Print the average scores
print(f"Average Precision: {avg_P:.4f}")
print(f"Average Recall: {avg_R:.4f}")
print(f"Average F1-Score: {avg_F1:.4f}")

In [7]:
# Calculate the average scores

print(f"Average Precision: {avg_P:.4f}")
print(f"Average Recall: {avg_R:.4f}")
print(f"Average F1-Score: {avg_F1:.4f}")

Average Precision: 0.9278
Average Recall: 0.9260
Average F1-Score: 0.9268


In [8]:
with open("flant5_bert_score.txt", "w") as file:
        file.write(str(avg_P) + "\n")

with open("flant5_bert_recall.txt", "w") as file:
        file.write(str(avg_R) + "\n")

with open("flant5_bert_f1.txt", "w") as file:
        file.write(str(avg_F1) + "\n")

### BLEURT METRIC

In [ ]:
bleurt = load("bleurt", module_type="metric", checkpoint="BLEURT-20")
bleurt_output = bleurt.compute(predictions=predictions, references=references)

flant5_bleurt_score = bleurt_output['scores']
means = sum(flant5_bleurt_score)/len(flant5_bleurt_score)
flant5_bleurt_score.append(means)
print(means)    # from -infty to +infty

0.013222281817539289


In [ ]:
with open("flant5_bleurt.txt", "w") as file:
    for number in flant5_bleurt_score:
        file.write(str(number) + "\n")

### METEOR METRIC

In [ ]:
meteor = evaluate.load('meteor')
meteor_output = meteor.compute(predictions=predictions, references=references)
flant5_meteor_score = meteor_output['meteor']
print(flant5_meteor_score)

[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


0.5613365763589081


In [ ]:
# Second version (PRETOKENIZED)
# Tokenize predictions
tokenized_predictions = [word_tokenize(pred) for pred in predictions]
# Join tokenized predictions
joined_predictions = [" ".join(tokens) for tokens in tokenized_predictions]

# Tokenize references
tokenized_references = [word_tokenize(ref) for ref in references]
# Join tokenized references
joined_references = [" ".join(tokens) for tokens in tokenized_references]

#meteor = evaluate.load('meteor')
meteor_output_tokenizedstrat = meteor.compute(predictions=joined_predictions, references=joined_references)

flant5_meteor_scorev2 = meteor_output_tokenizedstrat['meteor']
print(flant5_meteor_scorev2)

0.5613710627057403


In [ ]:
with open("flant5_meteor.txt", "w") as file:
    for number in [flant5_meteor_scorev2]:
        file.write(str(number) + "\n")

### chrF(++) metrics

In [ ]:
stacked_references = [[ref] for ref in references]
chrf = evaluate.load("chrf")
chrf_output = chrf.compute(predictions=predictions, references=stacked_references)
print(chrf_output) #from 0 to 100

{'score': 55.54839792716989, 'char_order': 6, 'word_order': 0, 'beta': 2}


In [ ]:
chrf_output_pp = chrf.compute(predictions=predictions, references=stacked_references, word_order=2)
print(chrf_output_pp) #from 0 to 100

{'score': 53.14253552811194, 'char_order': 6, 'word_order': 2, 'beta': 2}


In [ ]:
# Save the dictionaries to text files

with open('flant5_chrf.txt', 'w') as file:
    json.dump(chrf_output, file)

with open('flant5_chrf_pp.txt', 'w') as file:
    json.dump(chrf_output_pp, file)

# Load the dictionaries from the text files
#with open('flant5_chrf.txt', 'r') as file:
#    loaded_data = json.load(file)
# ...

### BLEU METRIC

In [ ]:
bleu = evaluate.load("bleu")
# bleu_output = bleu.compute(predictions=predictions, references=stacked_references)
print(bleu_output)

{'bleu': 0.30060211633826933, 'precisions': [0.5994552427965615, 0.34967695861861403, 0.23440678752925306, 0.1661782469946251], 'brevity_penalty': 1.0, 'length_ratio': 1.003201325439765, 'translation_length': 1983636, 'reference_length': 1977306}


In [ ]:
# Initialize NLTK's word tokenizer
nltk.download('punkt')  # Download necessary resources for tokenization

# Tokenize the sentences into words and lowercase them
ntokenized_predictions = [word_tokenize(sentence.lower()) for sentence in predictions]
ntokenized_references = [word_tokenize(sentence.lower()) for sentence in references]

# Join the tokens of each sentence back into a string
njoined_predictions = [" ".join(tokens) for tokens in ntokenized_predictions]
njoined_references = [" ".join(tokens) for tokens in ntokenized_references]

nstacked_references = [[ref] for ref in njoined_references]

bleu_outputv2 = bleu.compute(predictions=njoined_predictions, references=nstacked_references)
print(bleu_outputv2)

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


{'bleu': 0.31138116560728507, 'precisions': [0.6153380729844888, 0.363342783161821, 0.24355001525293044, 0.1726437549965899], 'brevity_penalty': 1.0, 'length_ratio': 1.003538690553916, 'translation_length': 1998178, 'reference_length': 1991132}


In [ ]:
with open('flant5_bleu.txt', 'w') as file:
    json.dump(bleu_outputv2, file)

In [ ]:
bleu_outputv3 = bleu.compute(predictions=njoined_predictions, references=nstacked_references, max_order=2)
print(bleu_outputv3) 

## Of course, the results with this little max_order are way better but such little context makes no sense

{'bleu': 0.47284103885303347, 'precisions': [0.6153380729844888, 0.363342783161821], 'brevity_penalty': 1.0, 'length_ratio': 1.003538690553916, 'translation_length': 1998178, 'reference_length': 1991132}
